In [44]:
import pandas as pd
import plotly.express as px

# Load your data
df = pd.read_csv('NoAeroRun.csv')

# Convert the times to milliseconds
start_time_ms = 8 * 60 * 60 * 1000 + 47 * 60 * 1000 + 27 * 1000 + 20
end_time_ms = 8 * 60 * 60 * 1000 + 49 * 60 * 1000 + 57 * 1000

# Indices and their corresponding times
start_index = 2046
end_index = 18957
time_interval = 0.009  # seconds
radius = 0.26035  # in meters
gear_ratio = 3.54


# Time difference and index difference
time_diff_ms = end_time_ms - start_time_ms
index_diff = end_index - start_index

df['Wheel_Speed'] = (df['D2_Motor_Speed'] * (2 * 3.141592653589793 * radius) / 60) / gear_ratio

df['IVT_Result_I'] = df['IVT_Result_I']*-1

df['IVT_Result_I'] = df['IVT_Result_I']/1000

df['Power'] = df['D1_DC_Bus_Voltage'] * df['IVT_Result_I']

# Calculate incremental energy used at each time point
df['Incremental_Energy'] = df['Power'] * time_interval  # Energy in Joules (Watt-seconds)

# Calculate the cumulative energy used
df['Total_Energy'] = df['Incremental_Energy'].cumsum()

# Time per index
time_per_index_ms = time_diff_ms / index_diff

# Create the new time column
df['adjusted_time_ms'] = start_time_ms + (df.index - start_index) * time_per_index_ms

# Function to convert milliseconds to video time format
def ms_to_video_time(ms):
    minutes = ms // 60000
    seconds = (ms % 60000) / 1000
    return f"{int(minutes):02}:{seconds:05.2f}"

df['time_on_video'] = df['adjusted_time_ms'].apply(ms_to_video_time)

# Filter the DataFrame to include only relevant indices
df_video = df[(df.index >= start_index) & (df.index <= end_index)]

# Create the plot
fig = px.line(df_video, x='time_on_video', y='Wheel_Speed', title='Speed over Time', labels={'Wheel_Speed': 'Car Speed (m/s)'})
fig.show()


In [45]:
df_video

TimeStamp  D1_Commanded_Torque  D1_DC_Bus_Voltage  \
2046  1718634548859.4763183594        17.5953000000     518.9350000000   
2047  1718634548868.4760742188        18.1000000000     518.9430000000   
2048  1718634548877.4758300781        15.5816000000     519.1000000000   
2049  1718634548886.4755859375        14.6000000000     520.0730000000   
2050  1718634548895.4750976562        17.1182000000     519.8480000000   
...                        ...                  ...                ...   
18953 1718634701018.1503906250         0.0000000000     515.5850000000   
18954 1718634701027.1499023438         0.0000000000     514.6720000000   
18955 1718634701036.1499023438         0.0000000000     513.9020000000   
18956 1718634701045.1496582031         0.0000000000     514.5740000000   
18957 1718634701054.1494140625         0.0000000000     514.4890000000   

       D2_Motor_Speed  IVT_Result_I   Wheel_Speed          Power  \
2046   113.8200000000  0.8074100000  0.8766001068 418.9933083500   
2047   123.3920000000  0.9042750000  0.9503201580 469.2671813250   
2048    94.4040000000  0.9699740000  0.7270651598 503.5135034000   
2049    25.5029000000  0.8188300000  0.1964140297 425.8513745900   
2050   -52.6278000000  0.4484900000 -0.4053201116 233.1466295200   
...               ...           ...           ...            ...   
18953    2.0000000000  0.1219420000  0.0154032702  62.8714660700   
18954    1.8722100000  0.1214920000  0.0144190782  62.5285306240   
18955    1.0000000000  0.1210430000  0.0077016351  62.2042397860   
18956    0.8722600000  0.1226300000  0.0067178282  63.1022096200   
18957    0.0000000000  0.1244300000  0.0000000000  64.0178662700   

       Incremental_Energy      Total_Energy    adjusted_time_ms time_on_video  
2046         3.7709397751    203.8436269162 31647020.0000000000     527:27.02  
2047         4.2234046319    208.0670315481 31647028.8687836304     527:27.03  
2048         4.5316215306    212.5986530787 31647037.7375672646     527:27.04  
2049         3.8326623713    216.4313154501 31647046.6063508950     527:27.05  
2050         2.0983196657    218.5296351157 31647055.4751345292     527:27.06  
...                   ...               ...                 ...           ...  
18953        0.5658431946 287155.6358241664 31796964.5248654708     529:56.96  
18954        0.5627567756 287156.1985809420 31796973.3936491050     529:56.97  
18955        0.5598381581 287156.7584191001 31796982.2624327354     529:56.98  
18956        0.5679198866 287157.3263389866 31796991.1312163696     529:56.99  
18957        0.5761607964 287157.9024997831 31797000.0000000000     529:57.00  

[16912 rows x 11 columns]

In [47]:
df_lap = df_video[(df_video['time_on_video'] >= '529:21.008') & (df_video['time_on_video'] <= '529:27.011')]
df_lap.to_csv('NoAeroLap.csv')

In [48]:
df_lap #start index = 1895, 1718634547500.5148925781 end index = 18704, 1718634698777.2141113281 = 0.08 kilowatt hours

TimeStamp  D1_Commanded_Torque  D1_DC_Bus_Voltage  \
14899 1718634664533.1875000000        23.8771000000     504.8350000000   
14900 1718634664542.1872558594        24.2000000000     506.8650000000   
14901 1718634664551.1870117188        24.8374000000     508.3650000000   
14902 1718634664560.1867675781        26.0000000000     509.0870000000   
14903 1718634664569.1862792969        26.7789000000     507.2170000000   
...                        ...                  ...                ...   
15572 1718634670590.0151367188        19.9000000000     508.8000000000   
15573 1718634670599.0151367188        20.1680000000     508.4640000000   
15574 1718634670608.0148925781        20.7000000000     507.4120000000   
15575 1718634670617.0146484375        20.9680000000     507.8450000000   
15576 1718634670626.0144042969        21.5000000000     507.8430000000   

       D2_Motor_Speed  IVT_Result_I  Wheel_Speed           Power  \
14899 1262.6600000000  8.9523800000 9.7245465723 4519.4747573000   
14900 1170.5600000000  8.0445000000 9.0152259798 4077.4754925000   
14901 1105.6300000000  6.7278400000 8.5151588129 3420.1983816000   
14902 1099.0500000000  5.9394500000 8.4644820540 3023.6967821500   
14903 1130.9600000000  5.5394100000 8.7102412299 2809.6829219700   
...               ...           ...          ...             ...   
15572 1191.4500000000  5.4156800000 9.1761131370 2755.4979840000   
15573 1194.1200000000  5.3389100000 9.1966765027 2714.6435342400   
15574 1198.6700000000  5.4014500000 9.2317189424 2740.7605474000   
15575 1200.7800000000  5.4977800000 9.2479693925 2792.0200841000   
15576 1199.1000000000  5.7112000000 9.2350306455 2900.3929416000   

       Incremental_Energy      Total_Energy    adjusted_time_ms time_on_video  
14899       40.6752728157 195173.2000582155 31761010.4760215245     529:21.01  
14900       36.6972794325 195209.8973376480 31761019.3448051549     529:21.02  
14901       30.7817854344 195240.6791230824 31761028.2135887891     529:21.03  
14902       27.2132710393 195267.8923941217 31761037.0823724195     529:21.04  
14903       25.2871462977 195293.1795404195 31761045.9511560537     529:21.05  
...                   ...               ...                 ...           ...  
15572       24.7994818560 217962.4278396473 31766979.1674058288     529:26.98  
15573       24.4317918082 217986.8596314555 31766988.0361894630     529:26.99  
15574       24.6668449266 218011.5264763821 31766996.9049730934     529:27.00  
15575       25.1281807569 218036.6546571390 31767005.7737567276     529:27.01  
15576       26.1035364744 218062.7581936134 31767014.6425403580     529:27.01  

[678 rows x 11 columns]

In [49]:
218062.7581936134 -195173.2000582155

22889.558135397907

In [19]:
fig = px.line(df_video, x='time_on_video', y='D1_DC_Bus_Voltage', title='Voltage over Time', labels={'D1_DC_Bus_Voltage': 'Voltage'})
fig.show()


In [72]:
fig = px.line(df_video, x='time_on_video', y='D1_Commanded_Torque', title='Torque over Time', labels={'D1_Commanded_Torque': 'Torque'})
fig.show()


In [73]:
fig = px.line(df_video, x='time_on_video', y='IVT_Result_I', title='Current over Time', labels={'IVT_Result_I': 'Current'})
fig.show()


In [75]:
df_video

TimeStamp  D1_Commanded_Torque  IVT_Result_I  \
2935  1718626746430.0935058594        28.6000000000  3.9930000000   
2936  1718626746439.0930175781        28.4424000000  5.6637200000   
2937  1718626746448.0922851562        28.4000000000  6.8549900000   
2938  1718626746457.0915527344        26.5089000000  6.4635100000   
2939  1718626746466.0910644531        26.0000000000  6.0510900000   
...                        ...                  ...           ...   
13854 1718626844694.0039062500         0.0000000000  0.0054494100   
13855 1718626844703.0031738281         0.0000000000  0.0050000000   
13856 1718626844712.0026855469         0.0000000000  0.0050000000   
13857 1718626844721.0019531250         0.0000000000  0.0052001000   
13858 1718626844730.0012207031         0.0000000000  0.0056500600   

       D2_Motor_Speed  D1_DC_Bus_Voltage  Wheel_Speed           Power  \
2935   763.1350000000     510.8060000000 5.8773873002 2039.6483580000   
2936   825.9120000000     509.3750000000 6.3608728467 2884.9573750000   
2937   811.5080000000     507.4490000000 6.2499384948 3478.5578205100   
2938   645.7360000000     509.8110000000 4.9732230414 3295.1684966100   
2939   368.9340000000     514.1100000000 2.8413950431 3110.9258799000   
...               ...                ...          ...             ...   
13854    0.0000000000      14.7775000000 0.0000000000    0.0805286563   
13855    0.0000000000      15.3225000000 0.0000000000    0.0766125000   
13856    0.0000000000      14.4219000000 0.0000000000    0.0721095000   
13857    0.0000000000      15.0113000000 0.0000000000    0.0780602611   
13858    0.0000000000      15.1000000000 0.0000000000    0.0853159060   

       Incremental_Energy      Total_Energy time_on_video  
2935        18.3568352220   7003.0998762115      00:00.01  
2936        25.9646163750   7029.0644925865      00:00.02  
2937        31.3070203846   7060.3715129711      00:00.03  
2938        29.6565164695   7090.0280294406      00:00.04  
2939        27.9983329191   7118.0263623597      00:00.04  
...                   ...               ...           ...  
13854        0.0007247579 269934.4714628436      01:38.28  
13855        0.0006895125 269934.4721523561      01:38.29  
13856        0.0006489855 269934.4728013416      01:38.30  
13857        0.0007025424 269934.4735038840      01:38.31  
13858        0.0007678432 269934.4742717271      01:38.31  

[10924 rows x 10 columns]

In [11]:
fig = px.line(df_video, x='time_on_video', y='Power', title='Power over Time')
fig.show()
